<a href="https://colab.research.google.com/gist/Abonia1/d95c3a4f8640bfaf0cceb3ee51fffcfd/llmops-with-mlflow.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# MLFlow with Langchain

In [ ]:
!pip -q install langchain huggingface_hub transformers sentence_transformers mlflow

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 3.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 41.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 kB 9.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 39.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 66.7 MB/s eta 0:00:00


In [ ]:
from langchain import PromptTemplate, HuggingFaceHub, LLMChain
from langchain.llms import HuggingFacePipeline
from transformers import AutoTokenizer, AutoModelForCausalLM, pipeline, AutoModelForSeq2SeqLM


import torch
import mlflow

tokenizer = AutoTokenizer.from_pretrained("google/flan-t5-small")

model = AutoModelForSeq2SeqLM.from_pretrained("google/flan-t5-small")
pipe = pipeline(
    "text2text-generation",
    model=model, 
    tokenizer=tokenizer, 
    max_length=100
)

local_llm = HuggingFacePipeline(pipeline=pipe)

In [ ]:
template = """Translate everything you see after this into French:{input}"""
prompt = PromptTemplate(template=template, input_variables=["input"])

llm_chain = LLMChain(prompt=prompt, 
                     llm=local_llm
                     )
question = "What is the capital of England?"
print(llm_chain.run(question))

Quel est le capital de l'Angleterre?


In [ ]:
template2 = """Answer the question comes after this {input}"""
prompt = PromptTemplate(template=template2, input_variables=["input"])

llm_chain = LLMChain(prompt=prompt, 
                     llm=local_llm
                     )

question = "What is the capital of England?"
print(llm_chain.run(question))

london


In [ ]:
template3 = """Summerize the content:  {input}"""
prompt = PromptTemplate(template=template3, input_variables=["input"])

llm_chain = LLMChain(prompt=prompt, 
                     llm=local_llm
                     )

content = "The key innovation of the Transformer architecture is the self-attention mechanism, which allows the model to attend to different parts of the input sequence to learn relationships between words."
print(llm_chain.run(content))

The self-attention mechanism is a key innovation of the Transformer architecture.


In [ ]:
mlflow.langchain.log_model(
    lc_model=llm_chain,
    artifact_path="model",
    registered_model_name="flan-t5"
)

2023/05/09 16:51:05 WARNING mlflow: MLflow does not guarantee support for LLMChains outside of HuggingFaceHub and OpenAI, found <class 'langchain.llms.huggingface_pipeline.HuggingFacePipeline'>
Successfully registered model 'flan-t5'.
2023/05/09 16:51:12 INFO mlflow.tracking._model_registry.client: Waiting up to 300 seconds for model version to finish creation. Model name: flan-t5, version 1
Created version '1' of model 'flan-t5'.


In [ ]:
get_ipython().system_raw("mlflow ui --port 5000 &")# run tracking UI in the background

In [ ]:
#!pip install pyngrok --quiet
from pyngrok import ngrok

# Terminate open tunnels if exist
ngrok.kill()

# Setting the authtoken (optional)
# Get your authtoken from https://dashboard.ngrok.com/auth
NGROK_AUTH_TOKEN = "2PZ34qJwLxJZXjFj4qzPUP20gqU_5ULAaaVrnvHcS9LXm93AA"
ngrok.set_auth_token(NGROK_AUTH_TOKEN)



ngrok_tunnel = ngrok.connect(addr="5000", proto="http", bind_tls=True)
print("MLflow Tracking UI:", ngrok_tunnel.public_url)


MLflow Tracking UI: https://07fd-35-194-202-111.ngrok-free.app


In [ ]:
mlflow.end_run()

## MLFlow with transformer model

In [ ]:
import transformers
import mlflow

chat_pipeline = transformers.pipeline(model="microsoft/DialoGPT-medium")

#Log your LLM: To log your LLM to MLflow, use the Python code snippet below:

with mlflow.start_run():
  model_info = mlflow.transformers.log_model(
    transformers_model=chat_pipeline,
    artifact_path="chatbot",
    input_example="Hi there!"
  )


/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1219: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co/docs/transformers/main_classes/text_generation)
  warnings.warn(
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.
2023/05/09 16:55:48 WARNING mlflow.utils.requirements_utils: Found torch version (2.0.0+cu118) contains a local version label (+cu118). MLflow logged a pip requirement for t

In [ ]:
# Load as interactive pyfunc
chatbot = mlflow.pyfunc.load_model(model_info.model_uri)
chatbot.predict("What is the best books available on yoga?")

/usr/local/lib/python3.10/dist-packages/transformers/generation/utils.py:1219: UserWarning: You have modified the pretrained model configuration to control generation. This is a deprecated strategy to control generation and will be removed soon, in a future version. Please use a generation configuration file (see https://huggingface.co/docs/transformers/main_classes/text_generation)
  warnings.warn(
The attention mask and the pad token id were not set. As a consequence, you may observe unexpected behavior. Please pass your input's `attention_mask` to obtain reliable results.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
A decoder-only architecture is being used, but right-padding was detected! For correct generation results, please set `padding_side='left'` when initializing the tokenizer.


"I'm not sure, but I've heard good things about the book The Power of Yoga by Susan G. Komen."